# Laba

In [269]:
import numpy as np
import pandas as pd
from Classes.PercepTeacher import PerceptronTeacher
from Functions.function_of_activation import sigmoid, dsigmoid
from Functions.errorFunctions import MSE
from Classes.Layer import Layer
from Classes.LayerGen import LayerGenerator
from random import random
from Classes.Perceptron import Perceptron
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split


In [270]:
def batch_spliter(x, y, size, num):
    batches = list()
    for _ in range(num):
        js = np.random.shuffle(np.arange(size))
        batches.append((x[js][0], y[js][0]))
    return batches


In [271]:
models = pd.read_csv('../Data/DataLaba2/neo_task_smoted.csv')
X_train, X_test, y_train, y_test = train_test_split(models.drop(
    'hazardous', axis=1), models['hazardous'], test_size=0.5, random_state=42)


In [272]:
X_train.shape


(81996, 4)

In [273]:
layer_mass = LayerGenerator(sizes_of_input_layer=X_train.shape[1],
                                 sizes_of_hidden_layers=[
                                     X_train.shape[1]//2, X_train.shape[1]*4, X_train.shape[1]//2, X_train.shape[1]//4],
                                 sizes_of_output_layer=1,
                                 summators=[sum, sum, sum, sum, sum],
                                 dsummators=[lambda a: 1,
                                             lambda a: 1,
                                             lambda a: 1,
                                             lambda a: 1,
                                             lambda a: 1],
                                 activation_functions=[sigmoid,
                                                       sigmoid,
                                                       sigmoid,
                                                       sigmoid,
                                                       sigmoid],
                                 dactivation_functions=[dsigmoid,
                                                        dsigmoid,
                                                        dsigmoid,
                                                        dsigmoid,
                                                        dsigmoid],
                                 function_of_generation=lambda a,
                                 b: np.random.rand(a, b)).generate()
layer_mass


In [274]:
k = []
for i in layer_mass:
    k.append(i.get_weights())
    print(i.get_weights())


[[0.43329651 0.07255871 0.83161333 0.49933069]
 [0.19155914 0.67559278 0.94479875 0.7869299 ]]
[[0.27879286 0.59054908]
 [0.79191683 0.11197091]
 [0.73284221 0.86259897]
 [0.7709216  0.44079307]
 [0.62923788 0.69707786]
 [0.67589828 0.30217293]
 [0.06337928 0.60824276]
 [0.17615743 0.0051316 ]
 [0.91865935 0.61466981]
 [0.03751546 0.57832874]
 [0.87406768 0.2555332 ]
 [0.27088974 0.45461553]
 [0.5153865  0.90661386]
 [0.66811345 0.06548292]
 [0.07956691 0.67032245]
 [0.45934041 0.75187736]]
[[0.50341086 0.65179545 0.17289444 0.6674408  0.52236271 0.7681908
  0.72078435 0.02060488 0.19871559 0.84584503 0.37119386 0.93498167
  0.1357839  0.39098809 0.62811427 0.90976477]
 [0.22871553 0.69764751 0.5439629  0.15016581 0.8798251  0.76354715
  0.95489148 0.40126417 0.88015051 0.74718064 0.67185064 0.59596749
  0.32921631 0.80656377 0.51870839 0.77784749]]
[[0.0603362  0.61281473]]
[[0.13988301]]


In [275]:
teacher = PerceptronTeacher(layers=layer_mass,
                                 step=0.00001,
                                 batch_spliter=lambda a, b: batch_spliter(
                                     a, b, a.shape[0]//2, 1),
                                 epochs=5000,
                                 error_function=MSE,
                                 derror_function=lambda x, y: 2 * x - 2 * y)


In [276]:
tl = teacher.teach(X_train.to_numpy()[:200], y_train.to_numpy()[:200])


In [277]:
for i in tl:
    print(i.get_weights())


[[ 0.11763005  0.35040097  1.10626179 -0.30532265]
 [-0.12410732  0.95343504  1.21944721 -0.01772345]]
[[0.33520517 0.64730762]
 [0.84832914 0.16872945]
 [0.78925452 0.9193575 ]
 [0.82733391 0.4975516 ]
 [0.68565019 0.7538364 ]
 [0.73231059 0.35893146]
 [0.11979159 0.6650013 ]
 [0.23256974 0.06189013]
 [0.97507166 0.67142834]
 [0.09392777 0.63508727]
 [0.93047999 0.31229174]
 [0.32730205 0.51137406]
 [0.57179881 0.96337239]
 [0.72452576 0.12224145]
 [0.13597923 0.72708098]
 [0.51575272 0.80863589]]
[[0.50809878 0.65651455 0.17805347 0.67237805 0.52737018 0.77296489
  0.72530885 0.02466213 0.20384476 0.85032097 0.37607754 0.93955336
  0.1408461  0.39556942 0.63270467 0.91469808]
 [0.23340345 0.70236661 0.54912192 0.15510306 0.88483257 0.76832124
  0.95941598 0.40532142 0.88527967 0.75165657 0.67673432 0.60053919
  0.3342785  0.8111451  0.52329879 0.7827808 ]]
[[0.10522667 0.65771777]]
[[0.25936716]]


In [278]:
for i, j in zip(k, tl):
    print(i - j.get_weights())


[[ 0.31566646 -0.27784226 -0.27464847  0.80465334]
 [ 0.31566646 -0.27784226 -0.27464847  0.80465334]]
[[-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]
 [-0.05641231 -0.05675853]]
[[-0.00468792 -0.00471911 -0.00515902 -0.00493725 -0.00500747 -0.00477409
  -0.0045245  -0.00405725 -0.00512916 -0.00447594 -0.00488368 -0.0045717
  -0.00506219 -0.00458133 -0.0045904  -0.00493331]
 [-0.00468792 -0.00471911 -0.00515902 -0.00493725 -0.00500747 -0.00477409
  -0.0045245  -0.00405725 -0.00512916 -0.00447594 -0.00488368 -0.0045717
  -0.00506219 -0.00458133 -0.0045904  -0.00493331]]
[[-0.04489048 -0.04490304]]
[[-0.11948415]]


In [279]:
a = Perceptron(tl)
res = [a.predict(i)[0] for i in X_test.to_numpy()]
print(MSE(res, y_test.to_numpy()))
for p, y in zip(res, y_test.to_numpy()):
    print(f'p:{p},\t y:{y},\t d:{abs(p-y)}')


0.2528791082368351
p:0.5541367554253622,	 y:0.0,	 d:0.5541367554253622
p:0.5541356338264076,	 y:0.0,	 d:0.5541356338264076
p:0.5541367166155137,	 y:1.0,	 d:0.44586328338448633
p:0.5541360066124074,	 y:0.0,	 d:0.5541360066124074
p:0.5541358611364468,	 y:0.0,	 d:0.5541358611364468
p:0.554136900458454,	 y:1.0,	 d:0.445863099541546
p:0.5541366503094793,	 y:1.0,	 d:0.44586334969052066
p:0.5541369776166056,	 y:0.0,	 d:0.5541369776166056
p:0.5541369235881408,	 y:0.0,	 d:0.5541369235881408
p:0.5541347595500129,	 y:0.0,	 d:0.5541347595500129
p:0.5541367693918808,	 y:1.0,	 d:0.44586323060811917
p:0.5541365435219354,	 y:1.0,	 d:0.4458634564780646
p:0.5541370425847927,	 y:0.0,	 d:0.5541370425847927
p:0.5541365717523803,	 y:1.0,	 d:0.4458634282476197
p:0.5541366986273784,	 y:1.0,	 d:0.44586330137262165
p:0.5541354780350293,	 y:0.0,	 d:0.5541354780350293
p:0.5541350705747207,	 y:0.0,	 d:0.5541350705747207
p:0.5541364882691397,	 y:0.0,	 d:0.5541364882691397
p:0.5541363333790414,	 y:1.0,	 d:0.44586366

In [284]:
np.array(res).mean(), np.array(res).std(), np.array(res).min()


(0.554136203778144, 7.143111306148908e-07, 0.5541342594128511)

In [288]:
np.partition(np.array(res), 5)[5]


0.5541343041678243

In [306]:

# -1.183786126545848e+31, 0.01, 100
r2_score(np.array(res), y_test), r2_score(np.array(res) >= np.array(res).mean(), y_test), r2_score(np.array(res) > np.partition(np.array(res), 40550)[40550], y_test)


(-495607781230.25946, -0.8311645544951942, -0.799228468954877)

In [282]:
(np.array(res) >= 0.5785810917137368).mean()


0.0

In [283]:
for i in tl:
    print(i.get_weights())

[[ 0.11763005  0.35040097  1.10626179 -0.30532265]
 [-0.12410732  0.95343504  1.21944721 -0.01772345]]
[[0.33520517 0.64730762]
 [0.84832914 0.16872945]
 [0.78925452 0.9193575 ]
 [0.82733391 0.4975516 ]
 [0.68565019 0.7538364 ]
 [0.73231059 0.35893146]
 [0.11979159 0.6650013 ]
 [0.23256974 0.06189013]
 [0.97507166 0.67142834]
 [0.09392777 0.63508727]
 [0.93047999 0.31229174]
 [0.32730205 0.51137406]
 [0.57179881 0.96337239]
 [0.72452576 0.12224145]
 [0.13597923 0.72708098]
 [0.51575272 0.80863589]]
[[0.50809878 0.65651455 0.17805347 0.67237805 0.52737018 0.77296489
  0.72530885 0.02466213 0.20384476 0.85032097 0.37607754 0.93955336
  0.1408461  0.39556942 0.63270467 0.91469808]
 [0.23340345 0.70236661 0.54912192 0.15510306 0.88483257 0.76832124
  0.95941598 0.40532142 0.88527967 0.75165657 0.67673432 0.60053919
  0.3342785  0.8111451  0.52329879 0.7827808 ]]
[[0.10522667 0.65771777]]
[[0.25936716]]
